In [1]:
import json
import os
import numpy as np
import requests
import pandas as pd
from bs4 import BeautifulSoup
import re
import pickle
import os
import time
import random
from tqdm import tqdm
import time
from tabulate import tabulate
import matplotlib.pyplot as plt
import seaborn as sns
import collections
from IPython.display import display

import spacy.cli
from spacy.language import Language
import math
import nltk
from nltk.tokenize import sent_tokenize

from IPython.display import display

In [2]:
nltk.download('punkt')
nltk.data.load('tokenizers/punkt/italian.pickle')

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/eleonoracocciu/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [62]:
path_risorse = "../ParlaMint-IT.txt"
path_dataset = "../dataset"
path_pickle = "../pickle/"

In [4]:
def save_dataframe(path, file_name, dataframe_to_save):
    
    try:
        dataframe_to_save.to_csv(path+"/"+file_name+".csv", index = False, sep = "\t")
        print("File salvato correttamente")
        
    except:
        print("Errore nel salvataggio")
    
    return 

In [5]:
os.getcwd()

'/Users/eleonoracocciu/Desktop/TESI_magistrale/ParlaMint-IT/notebook'

In [6]:
#nlp = spacy.load('it_core_news_lg')
#nlp.max_length = 1500000

In [7]:
#dizionario con le trascrizioni per ogni anno
diz_udienze_per_anno = {}

Costruiamo l'insieme delle udienze per ogni anno (ogni anno ha una cartella con i file .txt che contengono l'identificativo dell'udienza e l'udienza. Noi prendiamo, per ogni anno, tutte le udienze, senza identificativo, riunite in una lista.

In [8]:
for folder in os.listdir(path_risorse):
    
    #solo le cartelle degli anni
    if folder.isdigit():
        
        conto = 0
        path_cartella = path_risorse+"/{folder}".format(folder=folder)    
        
        #per ogni anno (cartella) prendo tutti i file .txt
        lista_file = [file for file in os.listdir(path_cartella) if '.txt' in file]
        print("Anno {}: {} file .txt".format(folder, len(lista_file)))
        
        #creo nel dizionario la chiave per quell'anno
        diz_udienze_per_anno[folder] = []
        
        #per ogni file nella cartella di quell'anno prendo le udienze
        for file_txt in lista_file:
            with open(path_cartella+"/"+file_txt, 'r') as file:
                
                lista_temp = file.readlines()
                
                #prendo solamente l'udienza e non l'identificativo dell’udienza 
                #(es. "ParlaMint-IT_2020-10-21-LEG18-Sed-267.u1”)
                lista_udienze = [udienza.split("\t")[1] for udienza in lista_temp]
                conto+=len(lista_udienze)
                
                #popolo il dizionario con le trascrizioni per ogni anno
                diz_udienze_per_anno[folder].extend(lista_udienze)
                
        print("Anno {}: {} udienze".format(folder, conto))
        print()

Anno 2013: 158 file .txt
Anno 2013: 11005 udienze

Anno 2014: 210 file .txt
Anno 2014: 15145 udienze

Anno 2015: 188 file .txt
Anno 2015: 13828 udienze

Anno 2017: 186 file .txt
Anno 2017: 10226 udienze

Anno 2019: 101 file .txt
Anno 2019: 7507 udienze

Anno 2020: 98 file .txt
Anno 2020: 5210 udienze

Anno 2018: 78 file .txt
Anno 2018: 5205 udienze

Anno 2016: 180 file .txt
Anno 2016: 11247 udienze



In [9]:
for anno in diz_udienze_per_anno:
    print("{}: {} udienze".format(anno, len(diz_udienze_per_anno[anno])))

2013: 11005 udienze
2014: 15145 udienze
2015: 13828 udienze
2017: 10226 udienze
2019: 7507 udienze
2020: 5210 udienze
2018: 5205 udienze
2016: 11247 udienze


In [10]:
def salva_udienze_per_anno_unificate(anno, udienze):
    
    flusso_dataset_completo_unificato = pd.DataFrame(udienze, columns=['Udienze_originali'])
    save_dataframe(path_dataset, "Udienze_ParlaMint_unificate_{}".format(anno), flusso_dataset_completo_unificato)

In [11]:
for anno in sorted(list(diz_udienze_per_anno)):
    salva_udienze_per_anno_unificate(anno, diz_udienze_per_anno[anno])

File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente


In [12]:
diz_udienze_per_anno.keys()

dict_keys(['2013', '2014', '2015', '2017', '2019', '2020', '2018', '2016'])

In [13]:
diz_udienze_per_anno['2013'][:20]

['La seduta è aperta (ore 9,31). Si dia lettura del processo verbale. BERGER, segretario, dà lettura del processo verbale della seduta antimeridiana del 3 ottobre. PRESIDENTE. Non essendovi osservazioni, il processo verbale è approvato.\n',
 "L'elenco dei senatori in congedo e assenti per incarico ricevuto dal Senato, nonché ulteriori comunicazioni all'Assemblea saranno pubblicati nell'allegato B al Resoconto della seduta odierna.\n",
 "Avverto che nel corso della seduta odierna potranno essere effettuate votazioni qualificate mediante il procedimento elettronico. Pertanto decorre da questo momento il termine di venti minuti dal preavviso previsto dall'articolo 119, comma 1, del Regolamento (ore 9,35).\n",
 '[[Domando di parlare.]] [[PRESIDENTE. Ne ha facoltà.]] Signora Presidente, prima avevo alzato la mano, ma lei non ha sollevato lo sguardo. Chiedo la votazione del processo verbale previa verifica del numero legale. PRESIDENTE. Senatore Endrizzi, avendo già dato per approvato il pro

In [14]:
totale = 0
for anno in diz_udienze_per_anno:
    print("{0:17}: {1} udienze".format("Dimensione del dataset dell'anno {}".format(anno), len(diz_udienze_per_anno[anno])))
    totale += len(diz_udienze_per_anno[anno])

print()
print("Totale: {}".format(totale))

Dimensione del dataset dell'anno 2013: 11005 udienze
Dimensione del dataset dell'anno 2014: 15145 udienze
Dimensione del dataset dell'anno 2015: 13828 udienze
Dimensione del dataset dell'anno 2017: 10226 udienze
Dimensione del dataset dell'anno 2019: 7507 udienze
Dimensione del dataset dell'anno 2020: 5210 udienze
Dimensione del dataset dell'anno 2018: 5205 udienze
Dimensione del dataset dell'anno 2016: 11247 udienze

Totale: 79373


In [15]:
diz_udienze_per_anno['2013']

['La seduta è aperta (ore 9,31). Si dia lettura del processo verbale. BERGER, segretario, dà lettura del processo verbale della seduta antimeridiana del 3 ottobre. PRESIDENTE. Non essendovi osservazioni, il processo verbale è approvato.\n',
 "L'elenco dei senatori in congedo e assenti per incarico ricevuto dal Senato, nonché ulteriori comunicazioni all'Assemblea saranno pubblicati nell'allegato B al Resoconto della seduta odierna.\n",
 "Avverto che nel corso della seduta odierna potranno essere effettuate votazioni qualificate mediante il procedimento elettronico. Pertanto decorre da questo momento il termine di venti minuti dal preavviso previsto dall'articolo 119, comma 1, del Regolamento (ore 9,35).\n",
 '[[Domando di parlare.]] [[PRESIDENTE. Ne ha facoltà.]] Signora Presidente, prima avevo alzato la mano, ma lei non ha sollevato lo sguardo. Chiedo la votazione del processo verbale previa verifica del numero legale. PRESIDENTE. Senatore Endrizzi, avendo già dato per approvato il pro

In [16]:
for ud in diz_udienze_per_anno['2016']:
    if "Comprendiamo che evidenziare all'interno della mozione il vincolo di destinazione delle somme a interventi strutturali sulla rete ferroviaria impatta" in ud:
        print(ud)

[[Domando di parlare per dichiarazione di voto.]] [[PRESIDENTE. Ne ha facoltà.]] Signor Presidente, certamente non possiamo che accogliere con favore il parere favorevole che il Governo ha espresso sulla nostra mozione. Comprendiamo che evidenziare all'interno della mozione il vincolo di destinazione delle somme a interventi strutturali sulla rete ferroviaria impatta sulla normativa che attualmente impone che il processo di privatizzazione, che ovviamente non riguarda solo Ferrovie ma anche altre partecipate dello Stato, sia finalizzato all'abbattimento del debito pubblico. Tuttavia - e in questo senso anticipo la volontà di Forza Italia di espungere dal testo il punto 3) - ci conforta il fatto che rimane il punto 4). C'è quindi un'intenzione e un interesse fortissimo e importante da parte del Governo, quindi anche da altre forze politiche che voteranno questa mozione, di superare il gap tecnologico esistente sull'alta capacità e sull'alta velocità, che va benino al Nord ma è assolutam

# Data cleaning

In [17]:
diz_parentesi_per_anno = {}

for anno in diz_udienze_per_anno:
    diz_parentesi_per_anno[anno] = {}
    square_list = []
    round_list = []
    frasi_con_quadre = []
    frasi_con_tonde = []

    for i in diz_udienze_per_anno[anno]:
        r1 = re.findall(r'\[.*?\]{1,}', i)
        r2 = re.findall(r'\(.*?\){1,}', i)
        square_list.extend(r1)
        round_list.extend(r2)
        if r1:
            frasi_con_quadre.append(i)
        if r2:
            frasi_con_tonde.append(i)

    square_list = list(set(square_list))
    round_list = list(set(round_list))
    
    diz_parentesi_per_anno[anno]['square_list'] = square_list
    diz_parentesi_per_anno[anno]['round_list'] = round_list
    diz_parentesi_per_anno[anno]['frasi_con_quadre'] = frasi_con_quadre
    diz_parentesi_per_anno[anno]['frasi_con_tonde'] = frasi_con_tonde

Vediamo, per ogni anno, quante frasi contengono parentesi quadre e tonde

In [18]:
lista_tot_square = []
lista_tot_round = []

for anno in diz_parentesi_per_anno:
    print(anno)
    print("{0:19}: {1}".format("Elementi nelle quadre", len(diz_parentesi_per_anno[anno]['square_list'])))
    print("{0:21}: {1}".format("Elementi nelle tonde", len(diz_parentesi_per_anno[anno]['round_list'])))
    lista_tot_square.extend(diz_parentesi_per_anno[anno]['square_list'])
    lista_tot_round.extend(diz_parentesi_per_anno[anno]['round_list'])
    print()
    
lista_tot_square = list(set(lista_tot_square))
lista_tot_round = list(set(lista_tot_round))

2013
Elementi nelle quadre: 2861
Elementi nelle tonde : 5640

2014
Elementi nelle quadre: 3994
Elementi nelle tonde : 9362

2015
Elementi nelle quadre: 3088
Elementi nelle tonde : 7664

2017
Elementi nelle quadre: 2306
Elementi nelle tonde : 5719

2019
Elementi nelle quadre: 2006
Elementi nelle tonde : 4389

2020
Elementi nelle quadre: 1100
Elementi nelle tonde : 4003

2018
Elementi nelle quadre: 1622
Elementi nelle tonde : 2556

2016
Elementi nelle quadre: 2361
Elementi nelle tonde : 6733



In [19]:
print("{0:19}: {1}".format("Totale elementi nelle quadre", len(lista_tot_square)))
print("{0:21}: {1}".format("Totale elementi nelle tonde", len(lista_tot_round)))

Totale elementi nelle quadre: 14753
Totale elementi nelle tonde: 42226


In [20]:
diz_parentesi_per_anno['2020']['square_list'][:50]

['[[Applausi. Brusio.]]',
 "[[Applausi dai Gruppi FIBP-UDC, L-SP-PSd'Az e del senatore Zaffini]]",
 '[[Applausi dai Gruppi PD, M5S, IV-PSI e Misto-LeU.]]',
 '[[Commenti del senatore La Russa.]]',
 '[[Applausi dal Gruppo FIBP-UDC e del senatore De Bertoldi]]',
 "[[Mercoledì 22 aprile h. 9,30 - Interrogazioni a risposta immediata, ai sensi dell'articolo 151- bis del Regolamento]]",
 "[[Gruppi 7 ore, di cui: M5S 1h 30' FI-BP 1h 7' L-SP-PSd'Az 1h 7' PD 49' Misto 40' FdI 38' IV-PSI 37' Aut (SVP-PATT, UV) 32' Dissenzienti 5']]",
 "[[Reiterati commenti dai Gruppi L-SP-PSd'Az, M5S e PD.]]",
 '[[Applausi dal Gruppo M5S e del senatore Ferrari]]',
 '[[PRESIDENTE. È iscritta a parlare la senatrice Evangelista. Ne ha facoltà.]]',
 '[[Applausi dal Gruppo PD e della senatrice De Petris.]]',
 '[[PRESIDENTE.È iscritto a parlare il senatore Salvini. Ne ha facoltà.]]',
 '[[Applausi della senatrice Bottici.]]',
 '[[Martedì 8 settembre h 16,30-20 - Doc . XXII- bis , n. 3 - Relazione della Commissione di in

In [21]:
diz_parentesi_per_anno['2020']['round_list'][:50]

['(e, dunque, rischiando fino a dieci anni e sei mesi di carcere, con un minimo di quattro anni e sei mesi)',
 '(mi riferisco, ovviamente, a chi propone queste cose)',
 '(resterei sul pericolo in concreto e non parlerei di pericolo in astratto)',
 '(quella documentata per tabulas )',
 '(le case rifugio e i centri antiviolenza)',
 '(non si capisce come mai non sia prevista la parità, perché mi sarei aspettata il 50 per cento, comunque siamo al 40)',
 "(perché sta all'Esecutivo dimostrare il contrario)",
 '(La seduta, sospesa alle ore 19,09, è ripresa alle ore 19,20)',
 '(ponte di Genova, Expo)',
 '(qualche volta lo scrive anche qualcuno che del Parlamento fa parte e a me questo colpisce)',
 '(DESI)',
 '(quindi i Comuni)',
 '(ottimale ipotizzarla per ora fino almeno al 2024)',
 '(La seduta, sospesa alle ore 14,19, è ripresa alle ore 17,02)',
 '(n. 19)',
 '(dove si concentrano le persone)',
 '(ore 13,23)',
 '(La seduta, sospesa alle ore 19,55, è ripresa alle ore 20,47)',
 '(capace sicuram

# Dataset cleaning

- **diz_udienze_per_anno** --> dizionario con le udienze per ogni anno
- **diz_parentesi_per_anno** --> dizionario con esempi di udienze contenenti parentesi quadre e tonde

Osservo quante volte, nei vari anni, compaioono le espressioni:
- **[[Domando di parlare]]**
- **[[Domando di parlare.]]**
- **[[PRESIDENTE. Ne ha facoltà.]]**
- **[[PRESIDENTE. Ne ha facoltà]]**

In [22]:
for anno in diz_udienze_per_anno:
    print(anno)
    cont1 = 0
    cont11 = 0
    cont2 = 0
    cont21 = 0

    for udienza in diz_udienze_per_anno[anno]:
        if '[[Domando di parlare]]' in udienza:
            cont1+=1
        if '[[Domando di parlare.]]' in udienza:
            cont11+=1
        if '[[PRESIDENTE. Ne ha facoltà.]]' in udienza:
            cont2+=1
        if '[[PRESIDENTE. Ne ha facoltà]]' in udienza:
            cont21+=1

    print("{}: {}".format('[[Domando di parlare]]', cont1))
    print("{}: {}".format('[[Domando di parlare.]]', cont11))
    print("{}: {}".format('[[PRESIDENTE. Ne ha facoltà.]]', cont2))
    print("{}: {}".format('[[PRESIDENTE. Ne ha facoltà]]', cont21))
    print()

2013
[[Domando di parlare]]: 0
[[Domando di parlare.]]: 3056
[[PRESIDENTE. Ne ha facoltà.]]: 3663
[[PRESIDENTE. Ne ha facoltà]]: 0

2014
[[Domando di parlare]]: 1
[[Domando di parlare.]]: 3781
[[PRESIDENTE. Ne ha facoltà.]]: 5185
[[PRESIDENTE. Ne ha facoltà]]: 0

2015
[[Domando di parlare]]: 0
[[Domando di parlare.]]: 3658
[[PRESIDENTE. Ne ha facoltà.]]: 5241
[[PRESIDENTE. Ne ha facoltà]]: 0

2017
[[Domando di parlare]]: 0
[[Domando di parlare.]]: 2009
[[PRESIDENTE. Ne ha facoltà.]]: 3492
[[PRESIDENTE. Ne ha facoltà]]: 0

2019
[[Domando di parlare]]: 0
[[Domando di parlare.]]: 1073
[[PRESIDENTE. Ne ha facoltà.]]: 2008
[[PRESIDENTE. Ne ha facoltà]]: 0

2020
[[Domando di parlare]]: 0
[[Domando di parlare.]]: 703
[[PRESIDENTE. Ne ha facoltà.]]: 1269
[[PRESIDENTE. Ne ha facoltà]]: 0

2018
[[Domando di parlare]]: 0
[[Domando di parlare.]]: 801
[[PRESIDENTE. Ne ha facoltà.]]: 1414
[[PRESIDENTE. Ne ha facoltà]]: 0

2016
[[Domando di parlare]]: 0
[[Domando di parlare.]]: 2724
[[PRESIDENTE. Ne 

### Costruzione dell'Elenco storico dei Parlamentari della Repubblica
(https://www.senato.it/leg/ElencoParlamentari/Parla.html)

In [23]:
path_csv_pdf = '../pdf_e_csv_sigle/csv'

In [24]:
lista_nomi_parlamentari = []

#calcolo il totale delle righe di ogni dataset per sapere quanti nomi e cognomi di parlamentari
#dovrei ottenere alla fine
totale = 0

for file in tqdm(os.listdir(path_csv_pdf)):
    if 'senato.it' in file:
        df_tmp = pd.read_excel(path_csv_pdf+"/"+file, header=None) 
        
        #prendo per ogni file i nomi e cognomi
        lista_nomi_parlamentari.extend(df_tmp[0])
        
        #incremento il totale
        totale += df_tmp[0].shape[0]

100%|███████████████████████████████████████████| 32/32 [00:01<00:00, 28.71it/s]


In [25]:
print("Totale di nomi e cognomi di parlamentari nei file: {}".format(totale))

Totale di nomi e cognomi di parlamentari nei file: 8373


### Costruzione della lista dei cognomi dei parlamentari

In [26]:
lista_cognomi_parlamentari = []

for nome in tqdm(lista_nomi_parlamentari):
    parentesis = re.findall(r'\(.*?\){1,}', nome)
    nome = nome.replace(parentesis[0], '')
    nome = nome.strip()
    pattern_cognome = re.compile('(?:[A-Z]{1,}\'?\s?)?(?:[A-Z]{2,}|[A-Z]{1}\'\s?)(?:\s?\-?[A-Z]{2,})*')
    cognome = re.findall(pattern_cognome, nome)
    lista_cognomi_parlamentari.append(cognome[0])

100%|███████████████████████████████████| 8373/8373 [00:00<00:00, 107067.23it/s]


In [27]:
len(lista_nomi_parlamentari)

8373

In [28]:
#len(lista_cognomi_parlamentari)
#8373

In [29]:
#inserisco PRESIDENTE all'interno della lista dei cognomi in modo da individuare anche il presidente come 
#potenziale 'intruso' nelle udienze
lista_cognomi_parlamentari.append('PRESIDENTE')

In [30]:
#la lista dei congomi conterra' cognomi singoli, senza duplicati
lista_cognomi_parlamentari = sorted(list(set(lista_cognomi_parlamentari)))

In [31]:
len(lista_cognomi_parlamentari)

6337

In [32]:
lista_cognomi_parlamentari[:20]

['ABATE',
 'ABATERUSSO',
 'ABBADESSA',
 'ABBADO',
 'ABBATANGELO',
 'ABBATE',
 'ABBIATE',
 'ABBIATI',
 'ABBIATI GRECO CASOTTI',
 'ABBONDANZIERI',
 'ABBRUZZESE',
 'ABELLI',
 'ABENANTE',
 'ABETE',
 'ABIS',
 'ABOZZI',
 'ABRAMONTE',
 'ABRIGNANI',
 'ACCAME',
 'ACCIARINI']

### Costruzione del dizionario contenente le frasi con piu' interventi 
(**per l'esclusione delle udienze con 'intrusi'**)

- **diz_udienze_per_anno** --> dizionario con le udienze per ogni anno
- **diz_parentesi_per_anno** --> dizionario con esempi di udienze contenenti parentesi quadre e tonde
- **diz_udienze_con_piu_interventi_per_anno** --> dizionario con udienze contenenti intrusi

In [33]:
diz_udienze_per_anno['2013']

['La seduta è aperta (ore 9,31). Si dia lettura del processo verbale. BERGER, segretario, dà lettura del processo verbale della seduta antimeridiana del 3 ottobre. PRESIDENTE. Non essendovi osservazioni, il processo verbale è approvato.\n',
 "L'elenco dei senatori in congedo e assenti per incarico ricevuto dal Senato, nonché ulteriori comunicazioni all'Assemblea saranno pubblicati nell'allegato B al Resoconto della seduta odierna.\n",
 "Avverto che nel corso della seduta odierna potranno essere effettuate votazioni qualificate mediante il procedimento elettronico. Pertanto decorre da questo momento il termine di venti minuti dal preavviso previsto dall'articolo 119, comma 1, del Regolamento (ore 9,35).\n",
 '[[Domando di parlare.]] [[PRESIDENTE. Ne ha facoltà.]] Signora Presidente, prima avevo alzato la mano, ma lei non ha sollevato lo sguardo. Chiedo la votazione del processo verbale previa verifica del numero legale. PRESIDENTE. Senatore Endrizzi, avendo già dato per approvato il pro

**Costruiamo il dizionario che contiene, per ogni anno, le udienze che riportano piu' interventi al loro interno, per poterle poi scartare in fase di pulizia, prima della costruzione dei dataset**.

In [34]:
diz_udienze_con_piu_interventi_per_anno = {}

for anno in diz_udienze_per_anno:
    
    diz_udienze_con_piu_interventi_per_anno[anno] = {}
    pattern_cognomi_in_maiuscolo = re.compile('(?:[A-Z]{1,}\'?\s?)?(?:[A-Z]{2,}|[A-Z]{1}\'\s?)(?:\s?\-?[A-Z]{2,})*')
                
    for i, udienza in enumerate(tqdm(diz_udienze_per_anno[anno])):

        #dato che la parola PRESIDENTE compare sia solo fra parensetesi senza intervenire poi nella frase
        #sia fra parentesi e poi come 'intruso' vero e proprio, per individuare bene quando è un 'intruso',
        #cioe' quando interviene nella frase, elimino gia' in questa fase la dicitura fra parentesi quadre 
        #che sarebbe stata comunque rimossa in seguito
        if '[[PRESIDENTE. Ne ha facoltà.]]' in udienza or '[[PRESIDENTE. Ne ha facoltà]]' in udienza:
            udienza = udienza.replace('[[PRESIDENTE. Ne ha facoltà.]]', '')
            udienza = udienza.replace('[[PRESIDENTE. Ne ha facoltà]]', '')

        #cerco nella frase gli elementi in stampatello maiuscolo, che ci permettono di capire se ci sono altri
        #individui che si inseriscono nel discorso, ovvero gli 'intrusi'
        match = re.findall(pattern_cognomi_in_maiuscolo, udienza)
        match = list(set(match))

        #tengo nella lista dei match solo i cognomi dei parlamentari (se presenti)
        match = [string for string in match if string in lista_cognomi_parlamentari]

        #se sono rimasti cognomi di parlamentari nel match, aggiungo i match al dizionario, 
        #e metto come chiave l'indice della frase
        if match:
            diz_udienze_con_piu_interventi_per_anno[anno][i] = match

100%|███████████████████████████████████| 11247/11247 [00:05<00:00, 2072.80it/s]


In [35]:
diz_udienze_con_piu_interventi_per_anno['2013']

{0: ['BERGER', 'PRESIDENTE'],
 3: ['ENDRIZZI', 'PRESIDENTE'],
 10: ['GRANAIOLA', 'PRESIDENTE', 'DE MONTE', 'RUSSO'],
 16: ['PRESIDENTE', 'ARRIGONI'],
 17: ['PRESIDENTE'],
 22: ['PRESIDENTE'],
 28: ['PRESIDENTE'],
 30: ['PRESIDENTE'],
 34: ['PRESIDENTE'],
 36: ['PRESIDENTE', 'VOLPI', 'DE PETRIS'],
 38: ['BISINELLA', 'PRESIDENTE'],
 43: ['PRESIDENTE'],
 46: ['MAURO', 'PRESIDENTE'],
 49: ['PRESIDENTE'],
 51: ['PRESIDENTE', 'DE PETRIS'],
 54: ['PRESIDENTE'],
 61: ['PRESIDENTE'],
 64: ['PRESIDENTE', 'DE PETRIS'],
 70: ['PRESIDENTE'],
 72: ['PRESIDENTE'],
 74: ['FUCKSIA',
  'PRESIDENTE',
  'LANZILLOTTA',
  'CROSIO',
  'BENCINI',
  'FAZZONE',
  'PETRAGLIA',
  'DE PETRIS',
  'PAGLIARI',
  'MARTELLI',
  'BISINELLA',
  'CATALFO',
  'ICHINO'],
 76: ['PETROCELLI', 'PRESIDENTE'],
 77: ["D'ALIA", 'PAGLIARI', 'PRESIDENTE'],
 78: ['DI BIAGIO', 'MARAN', 'PRESIDENTE'],
 82: ["D'ALIA", 'PRESIDENTE'],
 86: ['PRESIDENTE'],
 87: ['PRESIDENTE'],
 93: ['PRESIDENTE'],
 95: ['PAGLIARI'],
 97: ['BULGARELLI', 'PA

In [36]:
tot = 0
for anno in diz_udienze_con_piu_interventi_per_anno:
    print("Anno {}: {} udienze con piu interventi".format(anno, len(diz_udienze_con_piu_interventi_per_anno[anno])))
    tot += len(diz_udienze_con_piu_interventi_per_anno[anno])
    
print()
print("Totale, per tutti gli anni, di udienze con interventi: {}".format(tot))

Anno 2013: 3492 udienze con piu interventi
Anno 2014: 5379 udienze con piu interventi
Anno 2015: 4618 udienze con piu interventi
Anno 2017: 3019 udienze con piu interventi
Anno 2019: 2133 udienze con piu interventi
Anno 2020: 1876 udienze con piu interventi
Anno 2018: 1554 udienze con piu interventi
Anno 2016: 3370 udienze con piu interventi

Totale, per tutti gli anni, di udienze con interventi: 25441


In [37]:
def handle_brackets(sentence, bracket):
    
    words_in_brackets = []
    
    lista_indici_punti_dopo_parentesi = []

    #se ho parentesi quadre elimino completamente tutto quello che si trova all'interno delle stesse
    if bracket == 'square':
        
        #creo la lista di tutte le parole fra parentesi
        words_in_brackets = re.findall(r'\[.*?\]{1,}', sentence)
        
        for word_in_bracket in words_in_brackets:
            sentence = sentence.replace(word_in_bracket, '')
            
        return sentence
        
    elif bracket == 'round':
        
        #creo la lista di tutte le parole fra parentesi
        words_in_brackets = re.findall(r'\(.*?\){1,}\.?', sentence)
        
    #creo la lista delle parole che sono fra parentesi ma senza parentesi
    words_not_in_brackets = [w.replace('[' if bracket == 'square' else '(', '').replace(']' if bracket == 'square' else ')', '') for w in words_in_brackets]
    
    #elementi da eliminare da words_in_brackets
    to_del = []
    
    for i, el1 in enumerate(words_in_brackets):
        
        #se fra parentesi appare uno dei termini nella lista elimino direttamente l'elemento fra parentesi
        for element in ['ore', 'applausi', 'Applausi', 'votazione', 'Allegato', 'allegato', \
                        'art.', 'richiesta', 'Brusìo', 'brusìo', 'Domando di parlare.',
                       'Domando di parlare','votazione', 'Vedi', 'vedi', 'testo', 'cartelli']:
            if element in el1:
                sentence = sentence.replace(el1, "")
                #rimozione di spazi supplementari
                sentence = re.sub('\s{2,}', " ", sentence)
                to_del.append(el1)
        
        #se l'elemento fra parentesi ha due parole o più, elimino le parentesi, ovvero sostituisco l'elemento
        #con il suo corrispondente senza parentesi, ma modifico la frase in questo modo:
        #se dopo le parentesi c'e' un punto allora tolgo le parentesi ma faccio precedere la frase da una virgola;
        #se dopo le parentesi c'e' una virgola o altro, inserisco la frase fra due trattini, in modo da sostituire
        #l'effetto delle parentesi
        if len(el1.split()) >=2:
            if el1[-1] == '.':
                sentence =  sentence.replace(el1, ", " + words_not_in_brackets[i])
            else:
                sentence = sentence.replace(el1, "- "  + \
                                        words_not_in_brackets[i] + ' -')
            to_del.append(el1) 
            
        #se fra parentesi c'e' solo un elemento elimino l'elemento
        elif len(el1.split()) == 1:
            sentence = sentence.replace(el1, '')
    
    #elimino gli elementi che avevano più parole all'interno delle parentesi da words_in_brackets
    #e ricalcolo di conseguenza words_not_in_brackets
    words_in_brackets = [el for el in words_in_brackets if el not in to_del]
    #print("2° ", words_in_brackets)
    words_not_in_brackets = [parola.replace('[' if bracket == 'square' else '(', '').replace(']' \
                                    if bracket == 'square' else ')', '') for parola in words_in_brackets]
    
    return sentence

In [38]:
def regolarizza_abbreviazioni_leggi_e_decreti(sentence, abbreviazioni_e_traduzioni):

    for key in abbreviazioni_e_traduzioni:
        if key.lower() in sentence:
            sentence = sentence.replace(key.lower(), abbreviazioni_e_traduzioni[key].lower())
        elif key in sentence:
            sentence = sentence.replace(key, abbreviazioni_e_traduzioni[key].lower())
    
    return sentence

In [39]:
def clean_sentences(lista_di_interventi, anno):
    
    dataset_new = []
    
    for num_sent, sentence in enumerate(lista_di_interventi):
        
        #se una udienza ha un solo elemento o appartiene all'elenco delle udienze con intrusi 
        #continuo senza neanche processarla e quindi non la inserisco
        if len(sentence.split()) == 1 or num_sent in diz_udienze_con_piu_interventi_per_anno[anno]:
            continue
            
        else:
            #-------------------------------------Pulizia della punteggiatura----------------------------------

            #sostituisco le virgolette particolari con gli apici normali
            sentence = sentence.replace('“', "'")
            sentence = sentence.replace('”', "'")
            sentence = sentence.replace('‘', "'")
            sentence = sentence.replace('’', "'")
            sentence = sentence.replace('€', 'euro ')
            
            sentence = regolarizza_abbreviazioni_leggi_e_decreti(sentence, abbreviazioni_e_traduzioni)
            
            if 'nn.' in sentence:
                sentence = sentence.replace('nn.', '')
            if 'gg.' in sentence:
                sentence = sentence.replace('gg.', 'giorni ')
            
            if ', ministro per le riforme costituzionali e i rapporti con il Parlamento.' in sentence:
                sentence = sentence.replace(', ministro per le riforme costituzionali e i rapporti con il Parlamento.', '')
            
            #rimuovo eventuali segni di interpunzione duplicati
            sentence = re.sub('([-,;:!?]){2,}', r'\1', sentence)

            #se la punteggiatura non è separata a destra da uno spazio lo aggiungo
            sentence = re.sub('([,;:!?])', r'\1 ', sentence)
            
            #se un trattino non è separato da spazi li aggiungo
            sentence = re.sub('(-)', r' \1 ', sentence)

            #elimino eventuali spazi supplementari all'inizio e alla fine della frase
            sentence = sentence.strip()
            
            #-------------------------------------Pulizia delle parentesi-------------------------------------
            
            #gestisco eventuali parentesi quadre e tonde
            if '[' and ']' in sentence:
                sentence = handle_brackets(sentence, 'square')
            if '(' and ')' in sentence:
                sentence = handle_brackets(sentence, 'round')
            
            #gestisco eventuali parentesi quadre e tonde singole che erano così già nel testo originale
            sentence = sentence.replace("[", "")
            sentence = sentence.replace("]", "")
            sentence = sentence.replace("(", "")
            sentence = sentence.replace(")", "")
            
            #-------------------------------------Pulizia finale---------------------------------------------- 
            #rimozione di spazi supplementari
            sentence = re.sub('\s{2,}', " ", sentence)

            #elimino eventuali tag html
            pattern_html = re.compile('<.*?>')
            sentence = re.sub(pattern_html, "", sentence)
            
            #se alcuni segni di interpunzione sono separati a sinistra da uno spazio, elimino lo spazio
            sentence = re.sub('\s([.,;:!?])', r'\1', sentence)
                    
            #elimino intestazioni della frase come A: oppure A.R.: oppure A.R: oppure AR:
            pattern = re.compile('[A-Z]{1}.[A-Z]{1}.?:')
            sentence = re.sub(pattern, "", sentence)
            
            pattern = re.compile('[A-Z]{2}:')
            sentence = re.sub(pattern, "", sentence)
            
            pattern = re.compile('[A-Z]{1}:')
            sentence = re.sub(pattern, "", sentence)
            
            #elimino eventuali spazi supplementari all'inizio e alla fine della frase
            sentence = sentence.strip()
            
            #controllo che la frase non cominci con un segno di interpunzione
            punteggiatura = ['-','.',',',';',':','!','?']
            
            for p in punteggiatura:
                if sentence.startswith(p):
                    sentence = sentence[1:]
                    sentence = sentence.strip()
                    
            #elimino eventuali spazi supplementari all'inizio e alla fine della frase
            sentence = sentence.strip()
            
            if sentence:
                if len(sentence.split()) > 1:
                    if sentence[-1] not in ['.', ';', '?', '!']:
                        sentence = sentence + '.'
                    dataset_new.append(sentence)
        
    return dataset_new

- **diz_udienze_per_anno** --> dizionario con le udienze per ogni anno
- **diz_parentesi_per_anno** --> dizionario con esempi di udienze contenenti parentesi quadre e tonde
- **diz_udienze_con_piu_interventi_per_anno** --> dizionario con udienze contenenti intrusi

In [40]:
abbreviazioni_e_traduzioni = {}

df_abbreviazioni = pd.read_excel(path_csv_pdf+"/"+"Abbreviazioni_leggi_e_descreti_legislativi.xlsx", header=None) 

for row in df_abbreviazioni.itertuples():
    abbreviazioni_e_traduzioni[row._1] = row._2
    
print("Abbreviazioni e traduzioni")
print(abbreviazioni_e_traduzioni)

Abbreviazioni e traduzioni
{'Cost.': 'Costituzione', 'L. Cost.': 'Legge costituzionale', 'c.c.': 'codice civile', 'c.p.c.': 'codice di procedura civile', 'c.p.p.': 'codice di procedura penale', 'c.p.': 'codice penale', 'art.': 'Articolo', 'c.': 'Comma', 'L.': 'Legge', 'T.U.': 'Testo unico', 'D.L.': 'Decreto‐legge', 'D.Lgs': 'Decreto legislativo', 'D.P.R.': 'Decreto del Presidente della Repubblica', 'D.P.C.M.': 'Decreto del Presidente del Consiglio dei Ministri', 'D.M.': 'Decreto ministeriale', 'D. Interm.': 'Decreto interministeriale', 'Dir.': 'Direttiva', 'Reg.': 'Regolamento', 'G.U. suppl. suppl. ord.': 'Gazzetta ufficiale della Repubblica italiana Supplemento  Supplemento ordinario', 'G.U.C.E.': 'Gazzetta ufficiale delle Comunità europee', 'G.U. Sic.': 'Gazzetta ufficiale della Regione siciliana', 'B.U. Reg.': 'Bollettino ufficiale della regione', 'D.P.Reg.': 'Decreto del Presidente della regione', 'L.R.': 'Legge regionale', 'L.P.': 'Legge provinciale', 'R.D.': 'Regio decreto', 'R.D

**Puliamo tutte le udienze**

In [41]:
diz_udienze_pulite_per_anno = {}

for anno in tqdm(diz_udienze_per_anno):
    diz_udienze_pulite_per_anno[anno] = clean_sentences(diz_udienze_per_anno[anno], anno)

100%|█████████████████████████████████████████████| 8/8 [00:36<00:00,  4.62s/it]


In [42]:
diz_udienze_per_anno['2013'][:20]

['La seduta è aperta (ore 9,31). Si dia lettura del processo verbale. BERGER, segretario, dà lettura del processo verbale della seduta antimeridiana del 3 ottobre. PRESIDENTE. Non essendovi osservazioni, il processo verbale è approvato.\n',
 "L'elenco dei senatori in congedo e assenti per incarico ricevuto dal Senato, nonché ulteriori comunicazioni all'Assemblea saranno pubblicati nell'allegato B al Resoconto della seduta odierna.\n",
 "Avverto che nel corso della seduta odierna potranno essere effettuate votazioni qualificate mediante il procedimento elettronico. Pertanto decorre da questo momento il termine di venti minuti dal preavviso previsto dall'articolo 119, comma 1, del Regolamento (ore 9,35).\n",
 '[[Domando di parlare.]] [[PRESIDENTE. Ne ha facoltà.]] Signora Presidente, prima avevo alzato la mano, ma lei non ha sollevato lo sguardo. Chiedo la votazione del processo verbale previa verifica del numero legale. PRESIDENTE. Senatore Endrizzi, avendo già dato per approvato il pro

In [43]:
diz_udienze_pulite_per_anno['2013']

["L'elenco dei senatori in congedo e assenti per incarico ricevuto dal Senato, nonché ulteriori comunicazioni all'Assemblea saranno pubblicati nell'allegato B al Resoconto della seduta odierna.",
 "Avverto che nel corso della seduta odierna potranno essere effettuate votazioni qualificate mediante il procedimento elettronico. Pertanto decorre da questo momento il termine di venti minuti dal preavviso previsto dall'articolo 119, comma 1, del Regolamento.",
 'Nessuno al banco della Presidenza - io stavo leggendo - ha rilevato la sua richiesta. Le chiedo scusa. Magari la prossima volta formuli i suoi rilievi immediatamente, ma ora il processo verbale è già stato approvato.',
 "L'ordine del giorno reca il seguito della discussione del disegno di legge n. 1015. Ricordo che nella seduta di ieri è stata data lettura dei pareri della 1ᵃ e dalla 5ᵃ Commissione permanente e, su richiesta del relatore, l'Assemblea ha convenuto di rinviare il seguito della discussione alla seduta odierna. Invito i

In [44]:
tot = 0
for anno in diz_udienze_pulite_per_anno:
    print("{0:17}: {1} udienze".format("Dimensione del dataset dell'anno {}".format(anno), len(diz_udienze_pulite_per_anno[anno])))
    tot += len(diz_udienze_pulite_per_anno[anno])
    
print()
print("Totale per tutti gli anni: {} udienze ripulite".format(tot))

Dimensione del dataset dell'anno 2013: 7506 udienze
Dimensione del dataset dell'anno 2014: 9753 udienze
Dimensione del dataset dell'anno 2015: 9201 udienze
Dimensione del dataset dell'anno 2017: 7201 udienze
Dimensione del dataset dell'anno 2019: 5367 udienze
Dimensione del dataset dell'anno 2020: 3331 udienze
Dimensione del dataset dell'anno 2018: 3650 udienze
Dimensione del dataset dell'anno 2016: 7871 udienze

Totale per tutti gli anni: 53880 udienze ripulite


Controllo che non ci siano udienze con parentesi quadre e tonde

In [45]:
for anno in diz_udienze_pulite_per_anno:   
    for intervento in diz_udienze_pulite_per_anno[anno]:
        if '(' in intervento or ')' in intervento or '[' in intervento or ']' in intervento:
            print(anno, intervento)

Controllo che non ci siano udienze che cominciano con un segno di interpunzione

In [46]:
punteggiatura = ['-','.',',',';',':','!','?']

for anno in diz_udienze_pulite_per_anno:   
    for i, intervento in enumerate(diz_udienze_pulite_per_anno[anno]):
        for p in punteggiatura:
            if intervento.startswith(p):
                print(i, intervento)
                print()

2678 ..questo vuol dire che siamo molto preoccupati, e spero che l'impegno sulla valutazione d'impatto ambientale e sul rispetto della normativa sia davvero cogente. Lo ribadisco, siamo davvero veramente preoccupati per l'impatto ambientale sul territorio. Torno a ripetere, visto che è stato tutto l'asse portante del nostro ragionamento, che si tratta di un impatto ambientale, economico e sociale che rischia di essere altamente negativo. Per quanto riguarda poi la Strategia energetica nazionale, vorrei rispondere al relatore Romani, che nella sua attività di Ministro si è molto contraddistinto per avere messo a repentaglio lo sviluppo delle energie rinnovabili, forse qualcuno lo ricorderà. Penso sia necessario ridiscutere la SEN e fare un lavoro serio in un Paese serio, che cominci a discutere, a mettere i puntini sulle «i» e a indicare il percorso per la sua transizione energetica. Senatore Romani, magari lei è distratto anche quando le persone stanno parlando. Non le importa niente, 

In [47]:
def salva_udienze_ripulite_per_anno(anno, udienze):
    flusso_dataset_completo_ripulito = pd.DataFrame(udienze, columns=['Udienze ripulite'])
    save_dataframe(path_dataset, "Udienze_ParlaMint_ripulite_{}".format(anno), flusso_dataset_completo_ripulito)

In [48]:
for anno in diz_udienze_pulite_per_anno:
    salva_udienze_ripulite_per_anno(anno, diz_udienze_pulite_per_anno[anno])

File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente
File salvato correttamente


- **diz_udienze_per_anno** --> dizionario con le udienze per ogni anno
- **diz_parentesi_per_anno** --> dizionario con esempi di udienze contenenti parentesi quadre e tonde
- **diz_udienze_con_piu_interventi_per_anno** --> dizionario con udienze contenenti intrusi
- **diz_udienze_pulite_per_anno** --> dizionario con le udienze ripulite per ogni anno

# Creazione del flusso di frasi
In questa risorsa abbiamo delle udienze che possono contenere più frasi al loro interno, quindi le udienze verranno divise in frasi.

Il dataset sarà costruito nel seguente modo:
- **target -- target+1**
- **target -- target+5**
- **target -- target+10**
- **target -- target+20**
- **target -- target+30**
- **target -- frase random da altro talk**

Dunque:
- gli **interventi** saranno **segmentati in frasi utilizzando nltk**
- verrà creato un **dizionario che avrà come chiave l'intervento con il corrispondente numero (indice dell'iterazione nella lista degli interventi) e come valore la lista delle frasi al suo interno** (es.: {'intervento_1': [frase_1, frase2, frase3], 'intervento_2': [frase1, frase2]})
- verrà creata la **lista generale delle frasi, senza distinzione di interventi di appartenenza**
- verrà creata una **lista degli interventi di appartenenza delle frasi, con gli indici ripetuti tante volte quante sono le frasi di appartenenza** (es.:
    - lista_generale = [frase_1, frase_2, frase_3, frase_4, frase_5...]
    - lista_parallela = ['intervento_1','intervento_1','intervento_1','intervento_2', 'intervento_2'...])
- in questo modo sarà possibile:
    - **estrarre le frasi all'interno dello stesso intervento** (in base alle distanze già considerate in precedenza); 
    - **prendere frasi appartenenti ad altri interventi**: nel ciclo sulla lista di frasi flatten sarà formata ogni volta una **lista di elementi unici degli interventi (tranne l'intervento corrente)** e sarà estratta una **chiave** (intervento) **random** fra questi --> questa sarà la **chiave usata per selezionare una frase random dalla lista di frasi di quell'intervento nel dizionario degli interventi**.

In [49]:
def controlla_e_pulisci_frasi_tokenizzate(lista_frasi):
    
    lista_frasi_nuova = []
    
    for frase in lista_frasi:
        
        #controllo che la frase non cominci con un segno di interpunzione
        punteggiatura = ['-','.',',',';',':','!','?', '»']

        for p in punteggiatura:
            if frase.startswith(p):
                frase = frase[1:]
                frase = frase.strip()
    
        #rimozione di spazi supplementari
        frase = re.sub('\s{2,}', " ", frase)
            
        #elimino eventuali spazi supplementari all'inizio e alla fine della frase
        frase = frase.strip()
        
        lista_frasi_nuova.append(frase)
        
    return lista_frasi_nuova

In [50]:
#dizionario interventi
dizionario_interventi_per_anno = {}

for anno in diz_udienze_pulite_per_anno:
    dizionario_interventi_per_anno[anno] = {}
    dizionario_interventi_per_anno[anno]['interventi'] = {}
    
    #lista generale delle frasi, senza distinzione di interventi di appartenenza
    dizionario_interventi_per_anno[anno]['lista_frasi_totali_flatten'] = []
    
    #lista parallela a quella generale delle frasi, che ha come valori gli interventi di appartenenza delle frasi
    dizionario_interventi_per_anno[anno]['lista_interventi_appartenenza'] = []

    for i, intervento in enumerate(tqdm(diz_udienze_pulite_per_anno[anno])):
        #segmento l'intervento in frasi utilizzando nltk
        lista_frasi = sent_tokenize(intervento, language='italian')
        lista_frasi = controlla_e_pulisci_frasi_tokenizzate(lista_frasi)
        chiave = "intervento_{}".format(i)
        dizionario_interventi_per_anno[anno]['interventi'][chiave] = lista_frasi
        dizionario_interventi_per_anno[anno]['lista_frasi_totali_flatten'].extend(lista_frasi)
        dizionario_interventi_per_anno[anno]['lista_interventi_appartenenza'].extend([chiave for i in range(len(lista_frasi))])

100%|█████████████████████████████████████| 7871/7871 [00:04<00:00, 1686.22it/s]


In [51]:
diz_udienze_pulite_per_anno['2013'][3]

"L'ordine del giorno reca il seguito della discussione del disegno di legge n. 1015. Ricordo che nella seduta di ieri è stata data lettura dei pareri della 1ᵃ e dalla 5ᵃ Commissione permanente e, su richiesta del relatore, l'Assemblea ha convenuto di rinviare il seguito della discussione alla seduta odierna. Invito il senatore Segretario a dare lettura dell'ulteriore parere espresso dalla 5ᵃ Commissione permanente sugli emendamenti."

In [52]:
dizionario_interventi_per_anno['2013']['interventi']['intervento_1']

['Avverto che nel corso della seduta odierna potranno essere effettuate votazioni qualificate mediante il procedimento elettronico.',
 "Pertanto decorre da questo momento il termine di venti minuti dal preavviso previsto dall'articolo 119, comma 1, del Regolamento."]

In [53]:
len(dizionario_interventi_per_anno['2013']['lista_frasi_totali_flatten']), \
len(dizionario_interventi_per_anno['2013']['lista_interventi_appartenenza'])

(48057, 48057)

In [54]:
dizionario_interventi_per_anno['2013']['lista_frasi_totali_flatten'][1:3]

['Avverto che nel corso della seduta odierna potranno essere effettuate votazioni qualificate mediante il procedimento elettronico.',
 "Pertanto decorre da questo momento il termine di venti minuti dal preavviso previsto dall'articolo 119, comma 1, del Regolamento."]

In [55]:
dizionario_interventi_per_anno['2013']['lista_interventi_appartenenza'][1:3]

['intervento_1', 'intervento_1']

In [56]:
dizionario_interventi_per_anno['2013']['lista_interventi_appartenenza'][:10]

['intervento_0',
 'intervento_1',
 'intervento_1',
 'intervento_2',
 'intervento_2',
 'intervento_2',
 'intervento_3',
 'intervento_3',
 'intervento_3',
 'intervento_4']

In [57]:
#lista_numeri_interventi = list(range(len(dizionario_interventi)))

In [58]:
#random.choice(lista_numeri_interventi)

In [59]:
dizionario_interventi_per_anno.keys()

dict_keys(['2013', '2014', '2015', '2017', '2019', '2020', '2018', '2016'])

In [60]:
dizionario_interventi_per_anno['2013']['lista_frasi_totali_flatten'][1:3]

['Avverto che nel corso della seduta odierna potranno essere effettuate votazioni qualificate mediante il procedimento elettronico.',
 "Pertanto decorre da questo momento il termine di venti minuti dal preavviso previsto dall'articolo 119, comma 1, del Regolamento."]

In [63]:
with open('{}dizionario_interventi_per_anno.pickle'.format(path_pickle), 'wb') as handle:
     pickle.dump(dizionario_interventi_per_anno, handle)

# Training set extraction
#### Ricaviamo dei training set a complessità crescente

Il dataset sarà costruito nel seguente modo:
- **target -- target+1**
- **target -- target+5**
- **target -- target+10**
- **target -- target+20**
- **target -- target+30**
- **target -- frase random da altro talk**

**Per ogni anno, le frasi saranno prelevate all'interno dello stesso intervento, considerando le distanze succitate**. 
Nel caso in cui non siano presenti frasi a una certa distanza si va avanti; se non dovessero essere presenti frasi per un dataset a una certa distanza si oignorerà quella determinata distanza e si scriverà nella tesi che per quel dataset non erano presenti frasi a quella distanza.

- **diz_udienze_per_anno** --> dizionario con le udienze per ogni anno
- **diz_parentesi_per_anno** --> dizionario con esempi di udienze contenenti parentesi quadre e tonde
- **diz_udienze_con_piu_interventi_per_anno** --> dizionario con udienze contenenti intrusi
- **diz_udienze_pulite_per_anno** --> dizionario con le udienze ripulite per ogni anno
- **dizionario_interventi_per_anno** --> dizionario contenente:
    - **lista di frasi appartenenti ad ogni intervento** (dizionario che ha come chiavi i numeri degli interventi);
    - **lista totale delle frasi**, senza distinzione di appartenenza
    - **lista degli interventi di appartenenza**

In [64]:
dizionario_interventi_per_anno['2013']['lista_interventi_appartenenza']

['intervento_0',
 'intervento_1',
 'intervento_1',
 'intervento_2',
 'intervento_2',
 'intervento_2',
 'intervento_3',
 'intervento_3',
 'intervento_3',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_4',
 'intervento_5',
 'intervento_6',
 'intervento_6',
 'intervento_6',
 'intervento_7',
 'intervento_8',
 'intervento_9',
 'intervento_10',
 'intervento_11',
 'intervento_12',
 'intervento_12',
 'intervento_13',
 'intervento_13',
 'intervento_13',
 'intervento_13',
 'intervento_13',
 'intervento_14',
 'intervento_14',
 'intervento_15',
 'intervento_16',
 'intervento_16',
 'intervento_16',
 'intervento_16',
 'intervento_16',
 'intervento_16',
 'intervento_16',
 'intervento_16',
 'intervent

In [65]:
def create_df_vecchio(dizionario_interventi, dist, perc, frase_da_altro_intervento):
    
    """
    Esempio di dizionario interventi:
    {anno:
        {'interventi':{'intervento_1': [sent_1, sent_2],
                       'intervento_2': [sent_1]...,
                      },
        'lista_frasi_totali_flatten': [sent_1, sente_2, sent_3...],
        'lista_interventi_appartenenza: [intervento_1, intervento_1, intervento_2...]'
        }
    }
    """
    print("Lunghezza lista_frasi_totali_flatten: {}".format(len(dizionario_interventi['lista_frasi_totali_flatten'])))
    print("Lunghezza lista_interventi_appartenenza: {}".format(len(dizionario_interventi['lista_interventi_appartenenza'])))
    print()
    
    list_of_lists = []
    
    for (i, el), intervento in zip(enumerate(tqdm(dizionario_interventi['lista_frasi_totali_flatten'])), \
                                   dizionario_interventi['lista_interventi_appartenenza']):
        
        if i < len(dizionario_interventi['lista_frasi_totali_flatten']) - dist:
            
           
            if ((len(el.split()) == 1 or \
                len(dizionario_interventi['lista_frasi_totali_flatten'][i+1].split()) == 1) or \
                (len(dizionario_interventi['lista_frasi_totali_flatten'][i+dist].split()) == 1 and \
                not frase_da_altro_intervento)
                ):
                continue
            
            else:
                # la frase 2 segue la frase 1 --> Classe 0
                # inserisco due frasi che si seguono sia se dobbiamo generare il dataset prendendo un'udienza randomica
                # da un altro intervento, sia se la frase che stiamo prendendo a una certa distanza fa sempre parte 
                # dell'intervento che stiamo considerando
                if frase_da_altro_intervento or dizionario_interventi['lista_interventi_appartenenza'][i+dist] == intervento:
                    list_of_lists.append([dizionario_interventi['lista_frasi_totali_flatten'][i], \
                                          dizionario_interventi['lista_frasi_totali_flatten'][i+1], '0'])

                # normalmente prendo la frase a distanza dist dalla frase target
                # inserisco due frasi che non si seguono soltanto se la frase che stiamo prendendo a una certa distanza 
                # fa sempre parte dell'intervento che stiamo considerando
                if not frase_da_altro_intervento and dizionario_interventi['lista_interventi_appartenenza'][i+dist] == intervento:
                    # la frase 2 non segue la frase 1 --> Classe 1
                    list_of_lists.append([dizionario_interventi['lista_frasi_totali_flatten'][i], \
                                          dizionario_interventi['lista_frasi_totali_flatten'][i+dist], '1'])

                if frase_da_altro_intervento:
                    #genero una lista di interventi unici (tranne l'intervento corrente) da cui poter estrarre un
                    #intervento casuale e una frase casuale fra quelle al suo interno
                    lista_altri_interventi = list(set([interv for interv in dizionario_interventi['lista_interventi_appartenenza'] \
                                             if interv != intervento]))
                    
                    frase_scelta = ''
                    
                    while(len(frase_scelta.split()) == 1 or not frase_scelta):
                        #estraggo un intervento a caso dalla lista generata
                        intervento_scelto = random.choice(lista_altri_interventi)

                        #estraggo una frase a caso dalla lista delle frasi di quell'intervento
                        frase_scelta = random.choice(dizionario_interventi['interventi'][intervento_scelto])

                    #esempi negativi --> la frase 2 non segue la frase 1 --> Classe 1
                    list_of_lists.append([dizionario_interventi['lista_frasi_totali_flatten'][i], frase_scelta, '1'])
 

    if list_of_lists:

        np_array = np.array(list_of_lists, dtype=object)

        df = pd.DataFrame(np_array, columns=['Sentence_1', 'Sentence_2', "Class"])

        #calcolo le quantità di esempi positivi e negativi
        diz_count_classes = df['Class'].value_counts().to_dict()

        #prendo la quantità di esempi positivi (frasi che non sono consecutive)
        qty_positive_class = diz_count_classes['1']

        #calcolo la quantità di frasi da invertire a seconda del parametro della percentuale e arrotondo per eccesso
        #al numero intero più vicino
        sentences_to_invert = math.ceil(qty_positive_class / 100 * perc)

        #Costruisco la lista degli indici degli esempi, isolandoli
        idx_positive_examples = list(df[df['Class'] == '1'].index)

        #eseguo l'inversione delle frasi
        for idx in idx_positive_examples[:sentences_to_invert]:
            tmp = df.loc[idx, 'Sentence_1']
            df.loc[idx, 'Sentence_1'] = df.loc[idx, 'Sentence_2']
            df.loc[idx, 'Sentence_2'] = tmp

        #ordino il dataset in base alla colonna della Classe, in modo decrescente
        df.sort_values(by=['Class'], inplace = True, ascending = False)

        #resetto l'indice
        df.reset_index(inplace = True, drop = True)

        display(df)
        print()
        print("Caratteristiche del dataset con esempi positivi a distanza {} {}".format(dist, "(classe 1 = udienze random)" \
                                                                                        if frase_da_altro_intervento else ""))
        print()
        print("Righe: {} \t Colonne: {}".format(df.shape[0], df.shape[1]))
        print()
        print("Dettaglio delle classi")
        print(df['Class'].value_counts())
        print()
        print("Percentuale di esempi positivi da invertire: {}%".format(perc))
        print("Sono stati invertiti {} esempi positivi".format(sentences_to_invert))
        print()
        print()
        
        return df
    
    else:
        return 

In [66]:
def create_df(dizionario_interventi, anno, dist, perc, frase_da_altro_intervento_da_altro_anno):
    
    """
    Esempio di dizionario interventi:
    {anno:
        {'interventi':{'intervento_1': [sent_1, sent_2],
                       'intervento_2': [sent_1]...,
                      },
        'lista_frasi_totali_flatten': [sent_1, sente_2, sent_3...],
        'lista_interventi_appartenenza: [intervento_1, intervento_1, intervento_2...]'
        }
    }
    """
    print("Lunghezza lista_frasi_totali_flatten: {}".format(len(dizionario_interventi[anno]['lista_frasi_totali_flatten'])))
    print("Lunghezza lista_interventi_appartenenza: {}".format(len(dizionario_interventi[anno]['lista_interventi_appartenenza'])))
    print()
    
    list_of_lists = []
    diz_idx_anno_e_intervento_scelti_random = {}
    
    for (i, el), intervento in zip(enumerate(tqdm(dizionario_interventi[anno]['lista_frasi_totali_flatten'])), \
                                   dizionario_interventi[anno]['lista_interventi_appartenenza']):
        
        if i < len(dizionario_interventi[anno]['lista_frasi_totali_flatten']) - dist:
            
           
            if ((len(el.split()) == 1 or \
                len(dizionario_interventi[anno]['lista_frasi_totali_flatten'][i+1].split()) == 1) or \
                (len(dizionario_interventi[anno]['lista_frasi_totali_flatten'][i+dist].split()) == 1 and \
                not frase_da_altro_intervento_da_altro_anno)
                ):
                continue
            
            else:
                # la frase 2 segue la frase 1 --> Classe 0
                # inserisco due frasi che si seguono sia se dobbiamo generare il dataset prendendo un'udienza randomica
                # da un altro intervento, sia se la frase che stiamo prendendo a una certa distanza fa sempre parte 
                # dell'intervento che stiamo considerando
                if frase_da_altro_intervento_da_altro_anno or dizionario_interventi[anno]['lista_interventi_appartenenza'][i+dist] == intervento:
                    list_of_lists.append([dizionario_interventi[anno]['lista_frasi_totali_flatten'][i], \
                                          dizionario_interventi[anno]['lista_frasi_totali_flatten'][i+1], '0'])

                # normalmente prendo la frase a distanza dist dalla frase target
                # inserisco due frasi che non si seguono soltanto se la frase che stiamo prendendo a una certa distanza 
                # fa sempre parte dell'intervento che stiamo considerando
                if not frase_da_altro_intervento_da_altro_anno and dizionario_interventi[anno]['lista_interventi_appartenenza'][i+dist] == intervento:
                    # la frase 2 non segue la frase 1 --> Classe 1
                    list_of_lists.append([dizionario_interventi[anno]['lista_frasi_totali_flatten'][i], \
                                          dizionario_interventi[anno]['lista_frasi_totali_flatten'][i+dist], '1'])

                    
                #------------------------SELEZIONO FRASE DA ALTRO INTERVENTO DI ALTRO ANNO --------------------------
                if frase_da_altro_intervento_da_altro_anno:
                    
                    frase_scelta = ''
                    
                    while(len(frase_scelta.split()) == 1 or not frase_scelta):
                        
                        lista_altri_anni = [year for year in dizionario_interventi if year != anno]
                        
                        anno_scelto = random.choice(lista_altri_anni)
                        
                        #genero una lista di interventi unici dell'anno scelto da cui poter estrarre un
                        #intervento casuale e una frase casuale fra quelle al suo interno
                        lista_altri_interventi = list(set([interv for interv in dizionario_interventi[anno_scelto]['lista_interventi_appartenenza']]))
                    
                        #estraggo un intervento a caso dalla lista generata
                        intervento_scelto = random.choice(lista_altri_interventi)

                        #estraggo una frase a caso dalla lista delle frasi di quell'intervento
                        frase_scelta = random.choice(dizionario_interventi[anno_scelto]['interventi'][intervento_scelto])

                    # la frase 2 non segue la frase 1 --> Classe 1
                    list_of_lists.append([dizionario_interventi[anno]['lista_frasi_totali_flatten'][i], frase_scelta, '1'])
                     
                    diz_idx_anno_e_intervento_scelti_random[i] = {}
                    diz_idx_anno_e_intervento_scelti_random[i] = {'anno_scelto': anno_scelto, 'intervento_scelto': intervento_scelto}

    if list_of_lists:

        np_array = np.array(list_of_lists, dtype=object)

        df = pd.DataFrame(np_array, columns=['Sentence_1', 'Sentence_2', "Class"])

        #calcolo le quantità di esempi positivi e negativi
        diz_count_classes = df['Class'].value_counts().to_dict()

        #prendo la quantità di esempi positivi (frasi che non sono consecutive)
        qty_positive_class = diz_count_classes['1']

        #calcolo la quantità di frasi da invertire a seconda del parametro della percentuale e arrotondo per eccesso
        #al numero intero più vicino
        sentences_to_invert = math.ceil(qty_positive_class / 100 * perc)

        #Costruisco la lista degli indici degli esempi, isolandoli
        idx_positive_examples = list(df[df['Class'] == '1'].index)

        #eseguo l'inversione delle frasi
        for idx in idx_positive_examples[:sentences_to_invert]:
            tmp = df.loc[idx, 'Sentence_1']
            df.loc[idx, 'Sentence_1'] = df.loc[idx, 'Sentence_2']
            df.loc[idx, 'Sentence_2'] = tmp

        #ordino il dataset in base alla colonna della Classe, in modo decrescente
        df.sort_values(by=['Class'], inplace = True, ascending = False)

        #resetto l'indice
        df.reset_index(inplace = True, drop = True)

        display(df)
        print()
        print("Caratteristiche del dataset con esempi positivi a distanza {} {}".format(dist, "(classe 1 = udienze random)" \
                                                                                        if frase_da_altro_intervento_da_altro_anno else ""))
        print()
        print("Righe: {} \t Colonne: {}".format(df.shape[0], df.shape[1]))
        print()
        print("Dettaglio delle classi")
        print(df['Class'].value_counts())
        print()
        print("Percentuale di esempi positivi da invertire: {}%".format(perc))
        print("Sono stati invertiti {} esempi positivi".format(sentences_to_invert))
        print()
        print()
        
        return df, diz_idx_anno_e_intervento_scelti_random
    
    else:
        return 

In [67]:
def assign_ids(df):
    
    df_new = df.copy()
    
    li = range(1,900000)
    
    columns_of_ids = random.sample(li, k=df.shape[0])
    
    df_new.insert(0, 'Id', columns_of_ids)
    
    print("Presenza di id duplicati: {}".format("Sì" if df_new['Id'].duplicated().any() else "No"))
    
    return df_new

In [68]:
def crea_dataset_per_anno_a_varie_distanze(dizionario_interventi_per_anno, anno):
    
    #creazione dataset normali
    df_dist_5, diz_idx_anno_e_intervento_scelti_random_5 = create_df(dizionario_interventi_per_anno, anno, 5, 30, False)
    df_dist_10, diz_idx_anno_e_intervento_scelti_random_10 = create_df(dizionario_interventi_per_anno, anno, 10, 30, False)
    df_dist_20, diz_idx_anno_e_intervento_scelti_random_20 = create_df(dizionario_interventi_per_anno, anno, 20, 30, False)
    df_dist_30, diz_idx_anno_e_intervento_scelti_random_30 = create_df(dizionario_interventi_per_anno, anno, 30, 30, False)
    df_random_speech, diz_idx_anno_e_intervento_scelti_random_rs = create_df(dizionario_interventi_per_anno, anno, 5, 30, True)
    
    
    diz_idx_anno_e_intervento_scelti_random_per_anno[anno] = {}
    diz_idx_anno_e_intervento_scelti_random_per_anno[anno]['df_dist_5'] = diz_idx_anno_e_intervento_scelti_random_5
    diz_idx_anno_e_intervento_scelti_random_per_anno[anno]['df_dist_10'] = diz_idx_anno_e_intervento_scelti_random_10
    diz_idx_anno_e_intervento_scelti_random_per_anno[anno]['df_dist_20'] = diz_idx_anno_e_intervento_scelti_random_20
    diz_idx_anno_e_intervento_scelti_random_per_anno[anno]['df_dist_30'] = diz_idx_anno_e_intervento_scelti_random_30
    diz_idx_anno_e_intervento_scelti_random_per_anno[anno]['df_random_speech'] = diz_idx_anno_e_intervento_scelti_random_rs
    
    #controllo che nei dataset non ci siano frasi di lunghezza 1
    for num_df, df in enumerate([df_dist_5, df_dist_10, df_dist_20, df_dist_30, df_random_speech]):
        print("Analizzo il dataset {}".format(num_df))
        try:
            for row in df.itertuples():
                if len(row.Sentence_1.split()) == 1 or len(row.Sentence_2.split()) == 1:
                    raise Exception("Ho trovato frasi di lunghezza 1")
        except Exception as e:
            print(num_df, row)

    print()
    print("--------------------------------------------------------------------------------------------")
    print()
    
    dizionario_dataset_per_anno[anno] = {}
    
    dizionario_dataset_per_anno[anno]['df_dist_5'] = df_dist_5
    dizionario_dataset_per_anno[anno]['df_dist_10'] = df_dist_10
    dizionario_dataset_per_anno[anno]['df_dist_20'] = df_dist_20
    dizionario_dataset_per_anno[anno]['df_dist_30'] = df_dist_30
    dizionario_dataset_per_anno[anno]['df_random_speech'] = df_random_speech
    
    '''
    dizionario_dataset_per_anno[anno]['df_dist_5_with_ids'] = df_dist_5_with_ids
    dizionario_dataset_per_anno[anno]['df_dist_10_with_ids'] = df_dist_10_with_ids
    dizionario_dataset_per_anno[anno]['df_dist_20_with_ids'] = df_dist_20_with_ids
    dizionario_dataset_per_anno[anno]['df_dist_30_with_ids'] = df_dist_30_with_ids
    dizionario_dataset_per_anno[anno]['df_random_speech_with_ids'] = df_random_speech_with_ids
    '''

In [69]:
dizionario_dataset_per_anno = {}

diz_idx_anno_e_intervento_scelti_random_per_anno = {}

for anno in dizionario_interventi_per_anno:
    
    print("Anno {}".format(anno))
    
    #passo al metodo il dizionario di uno specifico anno
    crea_dataset_per_anno_a_varie_distanze(dizionario_interventi_per_anno, anno)

Anno 2013
Lunghezza lista_frasi_totali_flatten: 48057
Lunghezza lista_interventi_appartenenza: 48057



100%|██████████████████████████████████| 48057/48057 [00:00<00:00, 79608.83it/s]


Sentence_1  \
0      Credo che la discussione e la riflessione atto...   
1      Più di tutti gli altri Paesi del Consiglio d'E...   
2      La chiusura degli OPG, come ho detto, va ad am...   
3      Voglio infatti sottolineare un aspetto positiv...   
4      Si tratta di servizi che auspico si sviluppino...   
...                                                  ...   
52745  Si tratta di un evento che avrà forse effetti ...   
52746  Tale evento testimonia - lasciatemelo dire - c...   
52747  Abbiamo così, signor Presidente, onorevoli sen...   
52748  Credo che ciò ci regali un rinnovato entusiasm...   
52749  «La Commissione programmazione economica, bila...   

                                              Sentence_2 Class  
0      Si tratta, infatti, di temi rispetto ai quali ...     1  
1      Deve essere effettivamente salvaguardato, e ad...     1  
2      Per quanto riguarda l'articolo 2, sono già sta...     1  
3      Quando si parla di bambini malati di cancro o ...     1  
4             Voglio solo aggiungere una considerazione.     1  
...                                                  ...   ...  
52745  Lasciatemi dire che questa portata storica è p...     0  
52746  Si tratta di un evento che avrà forse effetti ...     0  
52747  Questo l'abbiamo fatto per doveroso riguardo i...     0  
52748  Tale evento testimonia - lasciatemelo dire - c...     0  
52749  In merito agli emendamenti riferiti all'artico...     0  

[52750 rows x 3 columns]


Caratteristiche del dataset con esempi positivi a distanza 5 

Righe: 52750 	 Colonne: 3

Dettaglio delle classi
1    26375
0    26375
Name: Class, dtype: int64

Percentuale di esempi positivi da invertire: 30%
Sono stati invertiti 7913 esempi positivi


Lunghezza lista_frasi_totali_flatten: 48057
Lunghezza lista_interventi_appartenenza: 48057



100%|██████████████████████████████████| 48057/48057 [00:00<00:00, 90909.97it/s]


...

Sentence_1  \
0      Invito il senatore Segretario a verificare se ...   
1           I fatti sono gravi, sono attuali e costanti.   
2      Vedete, si parla di un sistema intero, in cui ...   
3      Il capo d'accusa dice infatti che «sfruttando ...   
4                          Altro che poveri disoccupati!   
...                                                  ...   
15029  I cittadini di Taranto pagano l'irresponsabili...   
15030  Noi, come Gruppo della Lega Nord, riteniamo ch...   
15031  Si possono fare tutte le polemiche che vogliam...   
15032  Ciò in quanto hanno soprattutto permesso l'int...   
15033  Poiché a breve sarà convocato un Consiglio di ...   

                                              Sentence_2 Class  
0                                     Il Senato approva.     1  
1      Sembriamo scordarci di tutte queste cose quand...     1  
2      Colleghi, il nostro dovere è valutare se l'att...     1  
3                      Ma ci dobbiamo mettere d'accordo.     1  
4      Se qualcuno, infatti, lamenta di essere stato ...     1  
...                                                  ...   ...  
15029  Signor Presidente, i problemi ambientali e san...     0  
15030  I cittadini di Taranto pagano l'irresponsabili...     0  
15031             Non siamo innamorati della continuità.     0  
15032  Noi, come Gruppo della Lega Nord, riteniamo ch...     0  
15033  Signor Presidente, per riprendere il discorso ...     0  

[15034 rows x 3 columns]


Caratteristiche del dataset con esempi positivi a distanza 30 

Righe: 15034 	 Colonne: 3

Dettaglio delle classi
1    7517
0    7517
Name: Class, dtype: int64

Percentuale di esempi positivi da invertire: 30%
Sono stati invertiti 2256 esempi positivi


Lunghezza lista_frasi_totali_flatten: 65352
Lunghezza lista_interventi_appartenenza: 65352



100%|████████████████████████████████████| 65352/65352 [03:10<00:00, 343.75it/s]


Sentence_1  \
0       Indìco la votazione nominale con scrutinio sim...   
1       Signor Presidente, intervengo solo per condivi...   
2       Siccome questo sarebbe uno degli argomenti non...   
3       Senatore Calderoli, non per gusto di polemica,...   
4       Colgo l'occasione per sottolineare, ancora una...   
...                                                   ...   
129833  Indìco la votazione nominale con scrutinio sim...   
129834                                   Non è approvata.   
129835  Metto ai voti la proposta di modifica del cale...   
129836                             Il Senato non approva.   
129837  Signor Presidente, chiedo la votazione del pro...   

                                               Sentence_2 Class  
0       Il senatore Moles ha facoltà di illustrare l'i...     1  
1                                      Il Senato approva.     1  
2       Signor Presidente, durante le operazioni di vo...     1  
3                                  Il Senato non approva.     1  
4       Qui, negli ultimi anni, si è creata questa str...     1  
...                                                   ...   ...  
129833                             Il Senato non approva.     0  
129834                           Dispongo la controprova.     0  
129835                                   Non è approvata.     0  
129836    Passiamo alla votazione dell'emendamento 7.226.     0  
129837                        Verifica del numero legale.     0  

[129838 rows x 3 columns]


Caratteristiche del dataset con esempi positivi a distanza 5 (classe 1 = udienze random)

Righe: 129838 	 Colonne: 3

Dettaglio delle classi
1    64919
0    64919
Name: Class, dtype: int64

Percentuale di esempi positivi da invertire: 30%
Sono stati invertiti 19476 esempi positivi


Analizzo il dataset 0
Analizzo il dataset 1
Analizzo il dataset 2
Analizzo il dataset 3
Analizzo il dataset 4

--------------------------------------------------------------------------------------------



**Salvo il dizionario che contiene i dataset per ogni anno**

In [70]:
with open('{}dizionario_dataset_per_anno.pickle'.format(path_pickle), 'wb') as handle:
     pickle.dump(dizionario_dataset_per_anno, handle)

In [71]:
dizionario_dataset_per_anno['2013']['df_dist_5']

Sentence_1  \
0      Credo che la discussione e la riflessione atto...   
1      Più di tutti gli altri Paesi del Consiglio d'E...   
2      La chiusura degli OPG, come ho detto, va ad am...   
3      Voglio infatti sottolineare un aspetto positiv...   
4      Si tratta di servizi che auspico si sviluppino...   
...                                                  ...   
52745  Si tratta di un evento che avrà forse effetti ...   
52746  Tale evento testimonia - lasciatemelo dire - c...   
52747  Abbiamo così, signor Presidente, onorevoli sen...   
52748  Credo che ciò ci regali un rinnovato entusiasm...   
52749  «La Commissione programmazione economica, bila...   

                                              Sentence_2 Class  
0      Si tratta, infatti, di temi rispetto ai quali ...     1  
1      Deve essere effettivamente salvaguardato, e ad...     1  
2      Per quanto riguarda l'articolo 2, sono già sta...     1  
3      Quando si parla di bambini malati di cancro o ...     1  
4             Voglio solo aggiungere una considerazione.     1  
...                                                  ...   ...  
52745  Lasciatemi dire che questa portata storica è p...     0  
52746  Si tratta di un evento che avrà forse effetti ...     0  
52747  Questo l'abbiamo fatto per doveroso riguardo i...     0  
52748  Tale evento testimonia - lasciatemelo dire - c...     0  
52749  In merito agli emendamenti riferiti all'artico...     0  

[52750 rows x 3 columns]

In [72]:
dizionario_dataset_per_anno['2013']['df_dist_5'].shape[0]

52750

In [73]:
def forma_dataset_unico_per_distanza(diz):
    
    diz_num_righe_per_distanze_per_anno = {}
    
    #verifico, per ogni anno, quante righe ci sono per quella distanza, per capire se il dataset unico viene 
    #costruito nel modo corretto
    for anno in diz:
        for distanza in diz[anno]:
            if distanza not in diz_num_righe_per_distanze_per_anno:
                diz_num_righe_per_distanze_per_anno[distanza] = {}
            diz_num_righe_per_distanze_per_anno[distanza][anno] = diz[anno][distanza].shape[0]
                
            
    for distanza in diz_num_righe_per_distanze_per_anno:
        print("{}: {}".format(distanza, diz_num_righe_per_distanze_per_anno[distanza]))
        print("Totale righe: {}".format(sum([val for k, val in diz_num_righe_per_distanze_per_anno[distanza].items()])))
        print()
        

    #distanza 5
    df_dist_5 = pd.DataFrame()
    for anno in diz:
        df_dist_5 = pd.concat([df_dist_5, diz[anno]['df_dist_5']])
        
    print("Distanza 5: {}".format(df_dist_5.shape[0]))
    
    #distanza 10
    df_dist_10 = pd.DataFrame()
    for anno in diz:
        df_dist_10 = pd.concat([df_dist_10, diz[anno]['df_dist_10']])
        
    print("Distanza 10: {}".format(df_dist_10.shape[0]))
    
    
    #distanza 20
    df_dist_20 = pd.DataFrame()
    for anno in diz:
        df_dist_20 = pd.concat([df_dist_20, diz[anno]['df_dist_20']])
        
    print("Distanza 20: {}".format(df_dist_20.shape[0]))
    
    
    #distanza 30
    df_dist_30 = pd.DataFrame()
    for anno in diz:
        df_dist_30 = pd.concat([df_dist_30, diz[anno]['df_dist_30']])
        
    print("Distanza 30: {}".format(df_dist_30.shape[0]))
    
    
    #random speech
    df_random_speech = pd.DataFrame()
    for anno in diz:
        df_random_speech = pd.concat([df_random_speech, diz[anno]['df_random_speech']])
        
    print("Random speech: {}".format(df_random_speech.shape[0]))
    
    
    return df_dist_5, df_dist_10, df_dist_20, df_dist_30, df_random_speech

In [74]:
df_dist_5, df_dist_10, \
df_dist_20, df_dist_30, df_random_speech = forma_dataset_unico_per_distanza(dizionario_dataset_per_anno)

df_dist_5: {'2013': 52750, '2014': 80234, '2015': 87062, '2017': 79600, '2019': 57890, '2020': 51272, '2018': 35730, '2016': 79286}
Totale righe: 523824

df_dist_10: {'2013': 36256, '2014': 54788, '2015': 59310, '2017': 56898, '2019': 40104, '2020': 39388, '2018': 24264, '2016': 55344}
Totale righe: 366352

df_dist_20: {'2013': 18980, '2014': 28242, '2015': 30662, '2017': 30152, '2019': 20828, '2020': 24122, '2018': 12360, '2016': 28962}
Totale righe: 194308

df_dist_30: {'2013': 10062, '2014': 14674, '2015': 16478, '2017': 15840, '2019': 10958, '2020': 14466, '2018': 6478, '2016': 15034}
Totale righe: 103990

df_random_speech: {'2013': 95414, '2014': 140616, '2015': 146924, '2017': 126168, '2019': 92532, '2020': 73102, '2018': 59070, '2016': 129838}
Totale righe: 863664

Distanza 5: 523824
Distanza 10: 366352
Distanza 20: 194308
Distanza 30: 103990
Random speech: 863664


In [75]:
save_dataframe(path_dataset, "df_dist_5", df_dist_5)

File salvato correttamente


In [76]:
save_dataframe(path_dataset, "df_dist_10", df_dist_10)

File salvato correttamente


In [77]:
save_dataframe(path_dataset, "df_dist_20", df_dist_20)

File salvato correttamente


In [78]:
save_dataframe(path_dataset, "df_dist_30", df_dist_30)

File salvato correttamente


In [79]:
save_dataframe(path_dataset, "df_random_speech", df_random_speech)

File salvato correttamente


In [80]:
#aggiunta dell'id di ogni evento a tutti i dataset
df_dist_5_with_ids = assign_ids(df_dist_5)
df_dist_10_with_ids = assign_ids(df_dist_10)
df_dist_20_with_ids = assign_ids(df_dist_20)
df_dist_30_with_ids = assign_ids(df_dist_30)
df_random_speech_with_ids = assign_ids(df_random_speech)

Presenza di id duplicati: No
Presenza di id duplicati: No
Presenza di id duplicati: No
Presenza di id duplicati: No
Presenza di id duplicati: No


In [81]:
save_dataframe(path_dataset, "df_dist_5_with_ids", df_dist_5_with_ids)

File salvato correttamente


In [82]:
save_dataframe(path_dataset, "df_dist_10_with_ids", df_dist_10_with_ids)

File salvato correttamente


In [83]:
save_dataframe(path_dataset, "df_dist_20_with_ids", df_dist_20_with_ids)

File salvato correttamente


In [84]:
save_dataframe(path_dataset, "df_dist_30_with_ids", df_dist_30_with_ids)

File salvato correttamente


In [85]:
save_dataframe(path_dataset, "df_random_speech_with_ids", df_random_speech_with_ids)

File salvato correttamente


In [86]:
dizionario_dataset_per_anno[anno]['df_dist_5']

Sentence_1  \
0              Passiamo alla votazione dell'articolo 29.   
1      Tra costoro, sempre secondo l'ordinanza, ci so...   
2      Quindi, non c'è uno scambio, perché egli è "là...   
3      Quindi, si verrebbe a verificare un fatto inau...   
4      Ora, non tocca a noi entrare nel merito delle ...   
...                                                  ...   
79281  Perché c'è voluta l'ondata di arresti del giug...   
79282  Ho parlato del MOSE, ma avrei potuto citare Ex...   
79283  Ricordiamolo: è stato compagno di strada dei r...   
79284  Non nascondo che, rispetto ai cantieri del fut...   
79285  Onorevoli colleghi, è notizia di pochi minuti ...   

                                              Sentence_2 Class  
0      Invito il senatore Segretario a verificare se ...     1  
1      Si dice che le norme che presiedono a questo p...     1  
2      La prima cosa è che le accuse non sono "poca r...     1  
3      Vedete, si parla di un sistema intero, in cui ...     1  
4      Il capo d'accusa dice infatti che «sfruttando ...     1  
...                                                  ...   ...  
79281  Ho parlato del MOSE, ma avrei potuto citare Ex...     0  
79282  Non nascondo che, rispetto ai cantieri del fut...     0  
79283  Lo definirei una sorta di anarchico struttural...     0  
79284  Tutti, anche alla luce del nuovo codice degli ...     0  
79285  Dario Fo, attore, autore e regista, ha innovat...     0  

[79286 rows x 3 columns]

In [87]:
for anno in dizionario_interventi_per_anno:
    for i, el in enumerate(dizionario_interventi_per_anno[anno]['lista_frasi_totali_flatten']):
        if "Comprendiamo che evidenziare all'interno della mozione il vincolo di destinazione delle somme a interventi strutturali sulla rete ferroviaria" in el:
            print(anno, i, el)


2016 43427 Comprendiamo che evidenziare all'interno della mozione il vincolo di destinazione delle somme a interventi strutturali sulla rete ferroviaria impatta sulla normativa che attualmente impone che il processo di privatizzazione, che ovviamente non riguarda solo Ferrovie ma anche altre partecipate dello Stato, sia finalizzato all'abbattimento del debito pubblico.


In [88]:
dizionario_interventi_per_anno['2016']['lista_interventi_appartenenza'][43357]

'intervento_5208'

In [89]:
dizionario_interventi_per_anno['2016']['interventi']['intervento_5211']

['Signor Presidente, certamente non possiamo che accogliere con favore il parere favorevole che il Governo ha espresso sulla nostra mozione.',
 "Comprendiamo che evidenziare all'interno della mozione il vincolo di destinazione delle somme a interventi strutturali sulla rete ferroviaria impatta sulla normativa che attualmente impone che il processo di privatizzazione, che ovviamente non riguarda solo Ferrovie ma anche altre partecipate dello Stato, sia finalizzato all'abbattimento del debito pubblico.",
 'Tuttavia - e in questo senso anticipo la volontà di Forza Italia di espungere dal testo il punto 3 - ci conforta il fatto che rimane il punto 4.',
 "C'è quindi un'intenzione e un interesse fortissimo e importante da parte del Governo, quindi anche da altre forze politiche che voteranno questa mozione, di superare il gap tecnologico esistente sull'alta capacità e sull'alta velocità, che va benino al Nord ma è assolutamente assente al Sud, come hanno detto i collega Mancuso e Uras per Si

In [90]:
dizionario_dataset_per_anno['2016']['df_dist_5']

Sentence_1  \
0              Passiamo alla votazione dell'articolo 29.   
1      Tra costoro, sempre secondo l'ordinanza, ci so...   
2      Quindi, non c'è uno scambio, perché egli è "là...   
3      Quindi, si verrebbe a verificare un fatto inau...   
4      Ora, non tocca a noi entrare nel merito delle ...   
...                                                  ...   
79281  Perché c'è voluta l'ondata di arresti del giug...   
79282  Ho parlato del MOSE, ma avrei potuto citare Ex...   
79283  Ricordiamolo: è stato compagno di strada dei r...   
79284  Non nascondo che, rispetto ai cantieri del fut...   
79285  Onorevoli colleghi, è notizia di pochi minuti ...   

                                              Sentence_2 Class  
0      Invito il senatore Segretario a verificare se ...     1  
1      Si dice che le norme che presiedono a questo p...     1  
2      La prima cosa è che le accuse non sono "poca r...     1  
3      Vedete, si parla di un sistema intero, in cui ...     1  
4      Il capo d'accusa dice infatti che «sfruttando ...     1  
...                                                  ...   ...  
79281  Ho parlato del MOSE, ma avrei potuto citare Ex...     0  
79282  Non nascondo che, rispetto ai cantieri del fut...     0  
79283  Lo definirei una sorta di anarchico struttural...     0  
79284  Tutti, anche alla luce del nuovo codice degli ...     0  
79285  Dario Fo, attore, autore e regista, ha innovat...     0  

[79286 rows x 3 columns]

In [91]:
dizionario_dataset_per_anno['2016']['df_dist_5'].loc[43357]

Sentence_1    Nel ricordare che il disegno di legge in esame...
Sentence_2    Infatti, la Corte costituzionale, nella nota s...
Class                                                         0
Name: 43357, dtype: object

In [92]:
df_dist_5

Sentence_1  \
0      Credo che la discussione e la riflessione atto...   
1      Più di tutti gli altri Paesi del Consiglio d'E...   
2      La chiusura degli OPG, come ho detto, va ad am...   
3      Voglio infatti sottolineare un aspetto positiv...   
4      Si tratta di servizi che auspico si sviluppino...   
...                                                  ...   
79281  Perché c'è voluta l'ondata di arresti del giug...   
79282  Ho parlato del MOSE, ma avrei potuto citare Ex...   
79283  Ricordiamolo: è stato compagno di strada dei r...   
79284  Non nascondo che, rispetto ai cantieri del fut...   
79285  Onorevoli colleghi, è notizia di pochi minuti ...   

                                              Sentence_2 Class  
0      Si tratta, infatti, di temi rispetto ai quali ...     1  
1      Deve essere effettivamente salvaguardato, e ad...     1  
2      Per quanto riguarda l'articolo 2, sono già sta...     1  
3      Quando si parla di bambini malati di cancro o ...     1  
4             Voglio solo aggiungere una considerazione.     1  
...                                                  ...   ...  
79281  Ho parlato del MOSE, ma avrei potuto citare Ex...     0  
79282  Non nascondo che, rispetto ai cantieri del fut...     0  
79283  Lo definirei una sorta di anarchico struttural...     0  
79284  Tutti, anche alla luce del nuovo codice degli ...     0  
79285  Dario Fo, attore, autore e regista, ha innovat...     0  

[523824 rows x 3 columns]

In [93]:
df_dist_5_with_ids

Id                                         Sentence_1  \
0      173553  Credo che la discussione e la riflessione atto...   
1      638764  Più di tutti gli altri Paesi del Consiglio d'E...   
2      666493  La chiusura degli OPG, come ho detto, va ad am...   
3      422873  Voglio infatti sottolineare un aspetto positiv...   
4      708953  Si tratta di servizi che auspico si sviluppino...   
...       ...                                                ...   
79281  212307  Perché c'è voluta l'ondata di arresti del giug...   
79282  702643  Ho parlato del MOSE, ma avrei potuto citare Ex...   
79283  107953  Ricordiamolo: è stato compagno di strada dei r...   
79284  275851  Non nascondo che, rispetto ai cantieri del fut...   
79285  651482  Onorevoli colleghi, è notizia di pochi minuti ...   

                                              Sentence_2 Class  
0      Si tratta, infatti, di temi rispetto ai quali ...     1  
1      Deve essere effettivamente salvaguardato, e ad...     1  
2      Per quanto riguarda l'articolo 2, sono già sta...     1  
3      Quando si parla di bambini malati di cancro o ...     1  
4             Voglio solo aggiungere una considerazione.     1  
...                                                  ...   ...  
79281  Ho parlato del MOSE, ma avrei potuto citare Ex...     0  
79282  Non nascondo che, rispetto ai cantieri del fut...     0  
79283  Lo definirei una sorta di anarchico struttural...     0  
79284  Tutti, anche alla luce del nuovo codice degli ...     0  
79285  Dario Fo, attore, autore e regista, ha innovat...     0  

[523824 rows x 4 columns]

In [94]:
for i, el in enumerate(dizionario_interventi_per_anno['2020']['lista_frasi_totali_flatten']):
    if 'Mancherà alla sua città.' in el:
        print(i, el)

36725 Mancherà alla sua città.


In [95]:
for anno in dizionario_interventi_per_anno:
    for i, el in enumerate(dizionario_interventi_per_anno[anno]['lista_frasi_totali_flatten']):
        if "Passiamo alla votazione dell'emendamento 1.76." in el:
            print(anno, i, el)

2015 64368 Passiamo alla votazione dell'emendamento 1.76.


In [96]:
dizionario_interventi_per_anno['2020']['lista_frasi_totali_flatten'][36674-30]

"La nostra risposta è che la vogliamo e dobbiamo cercare di mettere insieme le questioni del trasporto, non soltanto quello aereo, perché occorre l'intermodalità tra ferrovia e aereo."

In [97]:
dizionario_interventi_per_anno['2020']['lista_interventi_appartenenza'][18205+5]

'intervento_1630'

In [98]:
for i, el in enumerate(diz_udienze_pulite_per_anno['2013']):
    if "La Commissione programmazione economica, bilancio, esaminato il disegno di legge in titolo e preso atto dei chiarimenti forniti dal Governo, in base ai quali: - risulta confermata la disponibilità delle risorse del Fondo di rotazione per le politiche europee," in el:
        print(i, el)

6253 «La 1ᵃ Commissione permanente, esaminato il disegno di legge in titolo, considerando che le disposizioni ivi previste riguardano le materie sistema tributario e contabile dello Stato, previdenza sociale e coordinamento informativo, statistico e informatico dei dati dell'amministrazione statale, regionale e locale, riconducibili tutti alla competenza esclusiva dello Stato - articolo 117, comma secondo, lettere e -, o e r della Costituzione, nonché la materia tutela del lavoro, riconducibili alla potestà legislativa concorrente tra lo Stato e le Regioni - articolo 117, terzo comma della Costituzione -, esprime, per quanto di competenza, parere non ostativo, a condizione che: a sia soppresso il comma 17 dell'articolo 1, dal momento che la disposizione, nell'escludere che la decisione regionale in materia di incentivi possa prevedere requisiti aggiuntivi rispetto a quanto già previsto alla norma statale, è suscettibile di comprimere l'ambito di intervento riservato in materia alla com